In [1]:
import helpers
import pandas as pd
import numpy as np
import scipy.sparse as sparse
from collections import defaultdict
from itertools import chain
import random
import time
import matplotlib.pyplot as plt

train_read=pd.read_csv('./Datasets/ml-100k/train.csv', sep='\t', header=None)
test_read=pd.read_csv('./Datasets/ml-100k/test.csv', sep='\t', header=None)
train_ui, test_ui, user_code_id, user_id_code, item_code_id, item_id_code = helpers.data_to_csr(train_read, test_read)

In [2]:
train_ui

<943x1682 sparse matrix of type '<class 'numpy.int64'>'
	with 80000 stored elements in Compressed Sparse Row format>

# Let's prepare user and item features

### Item features

In [3]:
movies = pd.read_csv('./Datasets/ml-100k/u.item', sep='|', encoding='latin-1', header=None)
movies[:3]

0                  1            2   3   \
0   1   Toy Story (1995)  01-Jan-1995 NaN   
1   2   GoldenEye (1995)  01-Jan-1995 NaN   
2   3  Four Rooms (1995)  01-Jan-1995 NaN   

                                                  4   5   6   7   8   9   ...  \
0  http://us.imdb.com/M/title-exact?Toy%20Story%2...   0   0   0   1   1  ...   
1  http://us.imdb.com/M/title-exact?GoldenEye%20(...   0   1   1   0   0  ...   
2  http://us.imdb.com/M/title-exact?Four%20Rooms%...   0   0   0   0   0  ...   

   14  15  16  17  18  19  20  21  22  23  
0   0   0   0   0   0   0   0   0   0   0  
1   0   0   0   0   0   0   0   1   0   0  
2   0   0   0   0   0   0   0   1   0   0  

[3 rows x 24 columns]

In [4]:
movies=movies.astype(object)
id_date=pd.get_dummies(movies[[0,2]], ['id', 'date'])
id_date[:3]

id_1  id_2  id_3  id_4  id_5  id_6  id_7  id_8  id_9  id_10  ...  \
0     1     0     0     0     0     0     0     0     0      0  ...   
1     0     1     0     0     0     0     0     0     0      0  ...   
2     0     0     1     0     0     0     0     0     0      0  ...   

   date_30-Mar-1996  date_30-May-1997  date_30-Nov-1996  date_30-Oct-1995  \
0                 0                 0                 0                 0   
1                 0                 0                 0                 0   
2                 0                 0                 0                 0   

   date_30-Oct-1996  date_31-Dec-1997  date_31-Jan-1997  date_31-Jul-1996  \
0                 0                 0                 0                 0   
1                 0                 0                 0                 0   
2                 0                 0                 0                 0   

   date_31-May-1996  date_4-Feb-1971  
0                 0                0  
1                 0                0  
2                 0                0  

[3 rows x 1922 columns]

In [5]:
genres = pd.read_csv('./Datasets/ml-100k/u.genre', sep='|', header=None,
                     encoding='latin-1')
genres[:3]

0  1
0    unknown  0
1     Action  1
2  Adventure  2

In [6]:
item_genres=movies[np.arange(5,24)]
item_genres.columns=list(genres[0])

In [7]:
item_features_df=pd.concat([id_date, item_genres], axis=1).astype(int)
item_features_df

id_1  id_2  id_3  id_4  id_5  id_6  id_7  id_8  id_9  id_10  ...  \
0        1     0     0     0     0     0     0     0     0      0  ...   
1        0     1     0     0     0     0     0     0     0      0  ...   
2        0     0     1     0     0     0     0     0     0      0  ...   
3        0     0     0     1     0     0     0     0     0      0  ...   
4        0     0     0     0     1     0     0     0     0      0  ...   
...    ...   ...   ...   ...   ...   ...   ...   ...   ...    ...  ...   
1677     0     0     0     0     0     0     0     0     0      0  ...   
1678     0     0     0     0     0     0     0     0     0      0  ...   
1679     0     0     0     0     0     0     0     0     0      0  ...   
1680     0     0     0     0     0     0     0     0     0      0  ...   
1681     0     0     0     0     0     0     0     0     0      0  ...   

      Fantasy  Film-Noir  Horror  Musical  Mystery  Romance  Sci-Fi  Thriller  \
0           0          0       0        0        0        0       0         0   
1           0          0       0        0        0        0       0         1   
2           0          0       0        0        0        0       0         1   
3           0          0       0        0        0        0       0         0   
4           0          0       0        0        0        0       0         1   
...       ...        ...     ...      ...      ...      ...     ...       ...   
1677        0          0       0        0        0        0       0         0   
1678        0          0       0        0        0        1       0         1   
1679        0          0       0        0        0        1       0         0   
1680        0          0       0        0        0        0       0         0   
1681        0          0       0        0        0        0       0         0   

      War  Western  
0       0        0  
1       0        0  
2       0        0  
3       0        0  
4       0        0  
...   ...      ...  
1677    0        0  
1678    0        0  
1679    0        0  
1680    0        0  
1681    0        0  

[1682 rows x 1941 columns]

In [8]:
item_features=sparse.csr_matrix(item_features_df.values)
item_features

<1682x1941 sparse matrix of type '<class 'numpy.intc'>'
	with 6256 stored elements in Compressed Sparse Row format>

### User features

In [9]:
users = pd.read_csv('./Datasets/ml-100k/u.user', sep='|', encoding='latin-1', header=None)
users[:3]

0   1  2           3      4
0  1  24  M  technician  85711
1  2  53  F       other  94043
2  3  23  M      writer  32067

In [10]:
users=users.astype(object)
user_features_df=pd.get_dummies(users, ['id', 'age', 'sex','profesion','zip_code'])
item_features_df[:3]

id_1  id_2  id_3  id_4  id_5  id_6  id_7  id_8  id_9  id_10  ...  Fantasy  \
0     1     0     0     0     0     0     0     0     0      0  ...        0   
1     0     1     0     0     0     0     0     0     0      0  ...        0   
2     0     0     1     0     0     0     0     0     0      0  ...        0   

   Film-Noir  Horror  Musical  Mystery  Romance  Sci-Fi  Thriller  War  \
0          0       0        0        0        0       0         0    0   
1          0       0        0        0        0       0         1    0   
2          0       0        0        0        0       0         1    0   

   Western  
0        0  
1        0  
2        0  

[3 rows x 1941 columns]

In [11]:
train_ui

<943x1682 sparse matrix of type '<class 'numpy.int64'>'
	with 80000 stored elements in Compressed Sparse Row format>

In [12]:
user_features=sparse.csr_matrix(user_features_df.values)
user_features

<943x1822 sparse matrix of type '<class 'numpy.uint8'>'
	with 4715 stored elements in Compressed Sparse Row format>

# Model

#### LightFM with user and item features

In [13]:
from lightfm import LightFM
from lightfm.evaluation import precision_at_k

for loss in ['logistic', 'bpr', 'warp']:

    model = LightFM(no_components=10, loss=loss)
    model.fit(train_ui, user_features=user_features, item_features=item_features, epochs=30, num_threads=4)

    print(loss)
    print("Train precision: %.2f" % precision_at_k(model, test_interactions=train_ui, 
                                                   user_features=user_features, item_features=item_features, k=10).mean())
    print("Test precision: %.2f" % precision_at_k(model, test_interactions=test_ui, train_interactions=train_ui,
                                                  user_features=user_features, item_features=item_features, k=10).mean())

ModuleNotFoundError: No module named 'lightfm'

In [ ]:
def top_k_recommendations(model, user_features, item_features, user_code_id, item_code_id, topK=10):
    result=[]
    for user_code in range(test_ui.shape[0]):
        user_rated=train_ui.indices[train_ui.indptr[user_code]:train_ui.indptr[user_code+1]]
        scores = model.predict(user_code, np.arange(train_ui.shape[1]), user_features=user_features, item_features=item_features)
        
        scores[user_rated]=-np.inf # to put rated items at the end of the list
        
        top_items=[item_code_id[item] for item in np.argsort(-scores)[:topK]]
        result.append([user_code_id[user_code]]+list(chain(*zip(top_items,-np.sort(-scores)[:topK]))))
    return result

def estimate(model, user_features, item_features, user_code_id, item_code_id, test_ui):
    result=[]
    for user, item in zip(*test_ui.nonzero()):
        result.append([user_code_id[user], item_code_id[item], 
                       model.predict(user, np.array([item]), user_features=user_features, item_features=item_features)[0]])
    return result

In [14]:
top_n=pd.DataFrame(top_k_recommendations(model=model, user_features=user_features, item_features=item_features, user_code_id=user_code_id, item_code_id=item_code_id, topK=10))
top_n.to_csv('Recommendations generated/ml-100k/Ready_LightFM_reco.csv', index=False, header=False)

estimations=pd.DataFrame(estimate(model=model, user_features=user_features, item_features=item_features, user_code_id=user_code_id, item_code_id=item_code_id, test_ui=test_ui))
estimations.to_csv('Recommendations generated/ml-100k/Ready_LightFM_estimations.csv', index=False, header=False)

NameError: name 'top_k_recommendations' is not defined

#### Pure MF with LightFM

In [15]:
item_features_interactions=sparse.csr_matrix(item_features_df[[item_feature for item_feature in item_features_df.columns 
                                    if 'id_' in item_feature]].values)
user_features_interactions=sparse.csr_matrix(user_features_df[[user_feature for user_feature in user_features_df.columns 
                                    if 'id_' in user_feature]].values)

In [16]:
from lightfm import LightFM

model = LightFM(loss='warp')
model.fit(train_ui, user_features=user_features_interactions, item_features=item_features_interactions, epochs=30, num_threads=4)

from lightfm.evaluation import precision_at_k

print("Train precision: %.2f" % precision_at_k(model, test_interactions=train_ui, k=10).mean())
print("Test precision: %.2f" % precision_at_k(model, test_interactions=test_ui, train_interactions=train_ui, k=10).mean())

ModuleNotFoundError: No module named 'lightfm'

In [17]:
top_n=pd.DataFrame(top_k_recommendations(model=model, user_features=user_features_interactions, item_features=item_features_interactions, user_code_id=user_code_id, item_code_id=item_code_id, topK=10))
top_n.to_csv('Recommendations generated/ml-100k/Ready_LightFMpureMF_reco.csv', index=False, header=False)

estimations=pd.DataFrame(estimate(model=model, user_features=user_features_interactions, item_features=item_features_interactions, user_code_id=user_code_id, item_code_id=item_code_id, test_ui=test_ui))
estimations.to_csv('Recommendations generated/ml-100k/Ready_LightFMpureMF_estimations.csv', index=False, header=False)

NameError: name 'top_k_recommendations' is not defined

#### LightFM with user/item attributes only (without treating id as a feature)

In [18]:
item_features_only=sparse.csr_matrix(item_features_df[[item_feature for item_feature in item_features_df.columns 
                                    if 'id_' not in item_feature]].values)
user_features_only=sparse.csr_matrix(user_features_df[[user_feature for user_feature in user_features_df.columns 
                                    if 'id_' not in user_feature]].values)

In [22]:
from lightfm import LightFM

model = LightFM(loss='warp')
model.fit(train_ui, user_features=user_features_only, item_features=item_features_only, epochs=30, num_threads=4)

from lightfm.evaluation import precision_at_k

print("Train precision: %.2f" % precision_at_k(model, test_interactions=train_ui, 
                                    user_features=user_features_only, item_features=item_features_only, k=10).mean())
print("Test precision: %.2f" % precision_at_k(model, test_interactions=test_ui, train_interactions=train_ui,
                                    user_features=user_features_only, item_features=item_features_only, k=10).mean())

c:\users\adrian\appdata\local\programs\python\python38-32\lib\site-packages\lightfm\_lightfm_fast.py:9: UserWarning: LightFM was compiled without OpenMP support. Only a single thread will be used.
  warnings.warn('LightFM was compiled without OpenMP support. '


Train precision: 0.39
Test precision: 0.16


In [24]:
top_n=pd.DataFrame(top_k_recommendations(model=model, user_features=user_features_only, item_features=item_features_only, user_code_id=user_code_id, item_code_id=item_code_id, topK=10))
top_n.to_csv('Recommendations generated/ml-100k/Ready_LightFMcontent_reco.csv', index=False, header=False)

estimations=pd.DataFrame(estimate(model=model, user_features=user_features_only, item_features=item_features_only, user_code_id=user_code_id, item_code_id=item_code_id, test_ui=test_ui))
estimations.to_csv('Recommendations generated/ml-100k/Ready_LightFMcontent_estimations.csv', index=False, header=False)

NameError: name 'top_k_recommendations' is not defined

In [21]:
import evaluation_measures as ev

dir_path="Recommendations generated/ml-100k/"
super_reactions=[4,5]
test=pd.read_csv('./Datasets/ml-100k/test.csv', sep='\t', header=None)

df=ev.evaluate_all(test, dir_path, super_reactions)
display(df.iloc[:,:9])
display(df.iloc[:,np.append(0,np.arange(9, df.shape[1]))])

943it [00:00, 10622.43it/s]
943it [00:00, 9747.58it/s]
943it [00:00, 10554.65it/s]
943it [00:00, 9450.92it/s]
943it [00:00, 10058.79it/s]
943it [00:00, 10744.58it/s]
943it [00:00, 10390.37it/s]
943it [00:00, 10578.65it/s]
943it [00:00, 11388.05it/s]
943it [00:00, 11256.24it/s]
943it [00:00, 10166.93it/s]
943it [00:00, 10388.40it/s]
943it [00:00, 10058.69it/s]
943it [00:00, 10740.81it/s]
943it [00:00, 9636.75it/s]
943it [00:00, 10511.93it/s]
943it [00:00, 10864.37it/s]


Model      RMSE       MAE  precision    recall       F_1  \
0           Self_RP3Beta  3.704589  3.529397   0.286744  0.196524  0.191117   
0                Self_P3  3.702446  3.527273   0.282185  0.192092  0.186749   
0            Self_TopPop  2.508258  2.217909   0.188865  0.116919  0.118732   
0              Ready_SVD  0.949165  0.746667   0.093955  0.044969  0.051197   
0               Self_SVD  0.916330  0.720153   0.103393  0.044455  0.053177   
0         Ready_Baseline  0.949459  0.752487   0.091410  0.037652  0.046030   
0        Ready_SVDBiased  0.938146  0.739917   0.086532  0.037067  0.044832   
0         Self_GlobalAvg  1.125760  0.943534   0.061188  0.025968  0.031383   
0           Ready_Random  1.510030  1.211848   0.050053  0.022367  0.025984   
0            Ready_I-KNN  1.030386  0.813067   0.026087  0.006908  0.010593   
0  Ready_I-KNNWithZScore  0.957701  0.752387   0.003712  0.001994  0.002380   
0    Ready_I-KNNBaseline  0.935327  0.737424   0.002545  0.000755  0.001105   
0   Ready_I-KNNWithMeans  0.935327  0.737424   0.002545  0.000755  0.001105   
0            Ready_U-KNN  1.023495  0.807913   0.000742  0.000205  0.000305   
0          Self_TopRated  2.508258  2.217909   0.000954  0.000188  0.000298   
0        Self_BaselineUI  0.967585  0.762740   0.000954  0.000170  0.000278   
0              Self_IKNN  1.018363  0.808793   0.000318  0.000108  0.000140   

       F_05  precision_super  recall_super  
0  0.221375         0.213948      0.251263  
0  0.216980         0.204185      0.240096  
0  0.141584         0.130472      0.137473  
0  0.065474         0.083906      0.073996  
0  0.070073         0.093884      0.079366  
0  0.061286         0.079614      0.056463  
0  0.058877         0.078004      0.057865  
0  0.041343         0.040558      0.032107  
0  0.033727         0.030687      0.023255  
0  0.016046         0.021137      0.009522  
0  0.002919         0.003433      0.002401  
0  0.001602         0.002253      0.000930  
0  0.001602         0.002253      0.000930  
0  0.000449         0.000536      0.000198  
0  0.000481         0.000644      0.000223  
0  0.000463         0.000644      0.000189  
0  0.000189         0.000000      0.000000

Model      NDCG       mAP       MRR      LAUC        HR  \
0           Self_RP3Beta  0.344598  0.207836  0.587953  0.595770  0.885472   
0                Self_P3  0.339114  0.204905  0.572157  0.593544  0.875928   
0            Self_TopPop  0.214651  0.111707  0.400939  0.555546  0.765642   
0              Ready_SVD  0.104672  0.048211  0.220757  0.519187  0.483563   
0               Self_SVD  0.107792  0.051281  0.200210  0.518957  0.475080   
0         Ready_Baseline  0.095957  0.043178  0.198193  0.515501  0.437964   
0        Ready_SVDBiased  0.094583  0.043013  0.202391  0.515202  0.433722   
0         Self_GlobalAvg  0.067695  0.027470  0.171187  0.509546  0.384942   
0           Ready_Random  0.055392  0.021602  0.137690  0.507713  0.338282   
0            Ready_I-KNN  0.024214  0.008958  0.048068  0.499885  0.154825   
0  Ready_I-KNNWithZScore  0.005137  0.002158  0.016458  0.497349  0.027572   
0    Ready_I-KNNBaseline  0.003444  0.001362  0.011760  0.496724  0.021209   
0   Ready_I-KNNWithMeans  0.003444  0.001362  0.011760  0.496724  0.021209   
0            Ready_U-KNN  0.000845  0.000274  0.002744  0.496441  0.007423   
0          Self_TopRated  0.001043  0.000335  0.003348  0.496433  0.009544   
0        Self_BaselineUI  0.000752  0.000168  0.001677  0.496424  0.009544   
0              Self_IKNN  0.000214  0.000037  0.000368  0.496391  0.003181   

   Reco in test  Test coverage   Shannon      Gini  
0      0.998197       0.193362  4.291821  0.960775  
0      1.000000       0.077201  3.875892  0.974947  
0      1.000000       0.038961  3.159079  0.987317  
0      0.997985       0.204906  4.408913  0.954288  
0      0.853022       0.147186  3.911356  0.971196  
0      1.000000       0.033911  2.836513  0.991139  
0      0.996076       0.166667  4.168354  0.964092  
0      1.000000       0.025974  2.711772  0.992003  
0      0.987911       0.187590  5.111878  0.906685  
0      0.402333       0.434343  5.133650  0.877999  
0      0.389926       0.067821  2.475747  0.992793  
0      0.482821       0.059885  2.232578  0.994487  
0      0.482821       0.059885  2.232578  0.994487  
0      0.602121       0.010823  2.089186  0.995706  
0      0.699046       0.005051  1.945910  0.995669  
0      0.600530       0.005051  1.803126  0.996380  
0      0.392153       0.115440  4.174741  0.965327